In [1]:
import sys, time, pickle, torch
sys.path.insert(0, '../Models')
sys.path.insert(0, '../Utils')
sys.path.insert(0, '../Preprocess')
import numpy as np
import pandas as pd
from ann import NeuralNet
from utils import my_completely_random_sample, conv_input_attri_to_word_attri,\
    collect_info_for_metric, save_info, random_state, load_prev_samples, prep_text_for_view
from preprocess_funcs import preprocess_pipelined, prepare_text, prepare_text_view_friendly
from captum._utils.models.linear_model import SkLearnLasso
from nltk.tokenize import word_tokenize

[nltk_data] Downloading package stopwords to /home/user/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/user/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
model = torch.load('../Models/ann_model.pt')

In [3]:
Train_df = pd.read_csv('../Data/Processed/train_df.csv')
Test_df = pd.read_csv('../Data/Processed/test_df.csv')
Y_train = Train_df['sentiment']
Y_test = Test_df['sentiment']
Y_train_tensor = torch.tensor(Y_train, dtype=torch.float).unsqueeze(dim=1)
Y_test_tensor = torch.tensor(Y_test, dtype=torch.float).unsqueeze(dim=1)


In [4]:
reviews_raw, targets, indices = my_completely_random_sample(Train_df, num_sample=50)

In [5]:
# reviews_raw, targets, indices = load_prev_samples(Train_df, 'lime_outs.pkl')

In [6]:
reviews_raw[4]

'Directed and co-written by Eytan Fox the writer/director of the highly acclaimed 2002 mini feature "Yossi & Jagger" (2002). This comparative epic, at 1hr 53 minutes, is another fine romantic drama in which we must deal with tragedy as well as celebrate the beauty and joy in life. Westerners, especially urban gay men like myself, need to be moved outside our safety zone and be informed of the real life and death struggle elsewhere to be able to love with equity.<br /><br />While "Yossi & Jagger" focused on a pair of gay lovers in the closeted confines of Israeli military service, "Ha Buah" is centred on a group of civilian friends, both straight and gay, who share a unit in the heart of Israel\'s generally gay-tolerant, but not always gay-friendly, capital Tel Aviv.<br /><br />"Ha Buah" opens with a dramatic border check point scene in which Noam (Ohad Knoller \x96 Yossi from "Yossi & Jagger") first meets handsome young Arab Ashraf (Yousef Sweid). Romance soon blooms \x96 but in that p

In [7]:
prep_text_for_view(reviews_raw[4])

['Directed',
 'and',
 'co-written',
 'by',
 'Eytan',
 'Fox',
 'the',
 'writer/director',
 'of',
 'the',
 'highly',
 'acclaimed',
 '2002',
 'mini',
 'feature',
 '"Yossi',
 '&',
 'Jagger"',
 '(2002).',
 'This',
 'comparative',
 'epic,',
 'at',
 '1hr',
 '53',
 'minutes,',
 'is',
 'another',
 'fine',
 'romantic',
 'drama',
 'in',
 'which',
 'we',
 'must',
 'deal',
 'with',
 'tragedy',
 'as',
 'well',
 'as',
 'celebrate',
 'the',
 'beauty',
 'and',
 'joy',
 'in',
 'life.',
 'Westerners,',
 'especially',
 'urban',
 'gay',
 'men',
 'like',
 'myself,',
 'need',
 'to',
 'be',
 'moved',
 'outside',
 'our',
 'safety',
 'zone',
 'and',
 'be',
 'informed',
 'of',
 'the',
 'real',
 'life',
 'and',
 'death',
 'struggle',
 'elsewhere',
 'to',
 'be',
 'able',
 'to',
 'love',
 'with',
 'equity.br',
 '',
 'While',
 '"Yossi',
 '&',
 'Jagger"',
 'focused',
 'on',
 'a',
 'pair',
 'of',
 'gay',
 'lovers',
 'in',
 'the',
 'closeted',
 'confines',
 'of',
 'Israeli',
 'military',
 'service,',
 '"Ha',
 'Buah"',


In [8]:
#define some containers to save some info
model_out_list, attr_list = [], []

In [9]:
from captum.attr import Lime
from captum.attr import visualization 

In [10]:
# lime = Lime(forward_func=model.forward)
lime = Lime(model, interpretable_model=SkLearnLasso(alpha=0.0025))

In [11]:
def generate_record(raw_review, target):
    data, data_vec, input_tfidf = preprocess_pipelined([raw_review]) #preprocess_pipelined expects a lits of strings        
    input_model = input_tfidf.to_dense()
    with torch.no_grad():
        pred_prob =  model.forward(input_model).detach().item()
        pred_class = 'Pos' if pred_prob > 0.5 else 'Neg' 
        true_class = 'Pos' if target > 0.5 else 'Neg' 
        attribution = lime.attribute(input_model, n_samples=5000, return_input_shape=True, show_progress=True)
        attr_score = torch.sum(attribution)    
        attr_class = 'Pos' if attr_score > 0.5 else 'Neg'
        raw_input = prep_text_for_view(raw_review) #raw_review.split()
        convergence_score = 0
        print(f'orig attri nonzero: {attribution.nonzero()}')
        word_attributions = conv_input_attri_to_word_attri(attribution, raw_review)
        #         print(f'word attributions {word_attributions}')
        #         print(f'pred_prob {pred_prob}')
        #         print(f'pred_class {pred_class}')
        #         print(f'true_class {true_class}')
        #         print(f'attribution {attribution}')
        #         print(f'attr_class {attr_class}')
        #         print(f'attr_score {attr_score}')
#         print(f'raw_input {raw_input}')

        
        #collect info for metrics later
        collect_info_for_metric(model_out_list, pred_prob, attr_list, attribution)
        
    
        visual_record = visualization.VisualizationDataRecord(word_attributions=word_attributions,
                                                         pred_prob=pred_prob,
                                                         pred_class=pred_class,
                                                         true_class=true_class,
                                                         attr_class=attr_class,
                                                         attr_score=attr_score,
                                                         raw_input=raw_input,
                                                         convergence_score=convergence_score)
        
        
        return visual_record
      
    

In [12]:
for i, (rev_raw, target) in enumerate(zip(reviews_raw, targets), start=1):
    visual_record = generate_record(rev_raw, target)
    print(visualization.visualize_text([visual_record])) #list because visualize_text expects a list of visual_records

/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/captum/attr/_core/lime.py:1088: UserWarning: Attempting to construct interpretable model with > 10000 features.This can be very slow or lead to OOM issues. Please provide a featuremask which groups input features to reduce the number of interpretablefeatures. 
  warnings.warn(
Lime attribution: 100%|████████████████████████████████████████████████████████████| 5000/5000 [00:11<00:00, 453.70it/s]


orig attri nonzero: tensor([[    0,  1924],
        [    0,  6405],
        [    0,  7570],
        [    0,  8576],
        [    0,  8767],
        [    0,  9078],
        [    0, 13704],
        [    0, 15278],
        [    0, 16059],
        [    0, 19434],
        [    0, 21531],
        [    0, 22791],
        [    0, 23514],
        [    0, 24830],
        [    0, 25412],
        [    0, 25749],
        [    0, 26178],
        [    0, 28431],
        [    0, 28883],
        [    0, 29813],
        [    0, 29998],
        [    0, 38720],
        [    0, 40439],
        [    0, 41823],
        [    0, 42102],
        [    0, 43412],
        [    0, 45463],
        [    0, 46055],
        [    0, 46362],
        [    0, 49526],
        [    0, 53621],
        [    0, 54577],
        [    0, 55615],
        [    0, 57665],
        [    0, 58873],
        [    0, 60068],
        [    0, 60121],
        [    0, 62325],
        [    0, 63182],
        [    0, 64400],
        [    0, 7207

/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/captum/attr/_core/lime.py:1088: UserWarning: Attempting to construct interpretable model with > 10000 features.This can be very slow or lead to OOM issues. Please provide a featuremask which groups input features to reduce the number of interpretablefeatures. 
  warnings.warn(


<IPython.core.display.HTML object>


Lime attribution: 100%|████████████████████████████████████████████████████████████| 5000/5000 [00:10<00:00, 458.57it/s]


...

/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/captum/attr/_core/lime.py:1088: UserWarning: Attempting to construct interpretable model with > 10000 features.This can be very slow or lead to OOM issues. Please provide a featuremask which groups input features to reduce the number of interpretablefeatures. 
  warnings.warn(


<IPython.core.display.HTML object>


Lime attribution: 100%|████████████████████████████████████████████████████████████| 5000/5000 [00:10<00:00, 471.84it/s]


orig attri nonzero: tensor([[    0,    39],
        [    0,  1231],
        [    0,  4501],
        [    0,  5468],
        [    0,  6677],
        [    0, 10223],
        [    0, 10367],
        [    0, 12511],
        [    0, 12618],
        [    0, 18135],
        [    0, 19841],
        [    0, 19961],
        [    0, 20211],
        [    0, 21973],
        [    0, 22901],
        [    0, 25365],
        [    0, 25999],
        [    0, 26143],
        [    0, 26225],
        [    0, 29157],
        [    0, 29161],
        [    0, 34431],
        [    0, 37126],
        [    0, 37708],
        [    0, 38721],
        [    0, 40269],
        [    0, 42808],
        [    0, 44060],
        [    0, 44364],
        [    0, 46651],
        [    0, 49915],
        [    0, 53668],
        [    0, 54452],
        [    0, 55130],
        [    0, 56573],
        [    0, 58304],
        [    0, 60740],
        [    0, 61602],
        [    0, 62198],
        [    0, 62962],
        [    0, 6582

<IPython.core.display.HTML object>


In [13]:
save_info(indices, reviews_raw, targets, model_out_list, attr_list, fname='lime_outs.pkl')

{'indices': [3555,
  23474,
  13833,
  12237,
  4632,
  9114,
  327,
  844,
  24631,
  17758,
  5654,
  19637,
  1462,
  24567,
  8536,
  1013,
  13913,
  8203,
  12999,
  20936,
  10982,
  866,
  22731,
  19996,
  6293,
  18922,
  13688,
  12690,
  24838,
  3707,
  5811,
  5400,
  3285,
  2277,
  4026,
  15629,
  12084,
  14787,
  2421,
  13503,
  21742,
  338,
  18429,
  14404,
  7464,
  8679,
  16240,
  20882,
  15145,
  6782,
  13615,
  24420,
  8581,
  21797,
  10057,
  15051,
  21480,
  153,
  18810,
  16401,
  8940,
  12167,
  21933,
  22489,
  14061,
  1267,
  24227,
  5876,
  19832,
  11042,
  7307,
  23696,
  3962,
  16021,
  10652,
  75,
  11424,
  74,
  22711,
  10178,
  18522,
  1427,
  11155,
  5434,
  7696,
  21546,
  24579,
  17529,
  21464,
  15887,
  12967,
  7162,
  19841,
  2706,
  21057,
  4097,
  4939,
  15201,
  2310,
  18632],
 'raw_reviews': ['This musical was not quite what I expected, foremost being there weren\'t many scenes between Brando and Sinatra. As it

In [14]:
# from lime.lime_text import LimeTextExplainer
# explainer = LimeTextExplainer(
#     class_names = ['negative', 'positive'],
#     bow=True
#   )

# def lime_pred_sentence(sentence):
#     if isinstance(sentence, str):
#         sentence = [sentence]
#     sent_prepped, sent_vec, sent_tensor = preprocess_pipelined(sentence)
#     print(f'sent tensor size {sent_tensor.size()}')
#     with torch.no_grad():
#         out = model(sent_tensor)
#         out_complement = 1-out
#         out_concat = torch.cat([out_complement, out], dim=1)
#         out_concat_np = out_concat.detach().numpy()
    
# #         print(f'{sent_prepped}')
# #         print(f'{sent_vec}')
# #         print(f'{sent_tensor}')
# #         print(f'{out_concat_np.shape}')
#         return out_concat_np

# for r in reviews_raw:
#     explanation = explainer.explain_instance(r, lime_pred_sentence)
#     explanation.show_in_notebook()